In [41]:
kerr_dir = '/work/yifan.wang/ringdown/t9_usev2data_3ogc/kerr_220_221.ini'
set_toffset = False
events_dir = './220_221/events.ini'

In [42]:
import numpy as np
import os,sys,glob,h5py

from pycbc.inference.io import loadfile
from pycbc.workflow import WorkflowConfigParser
from configparser import ConfigParser
from pycbc import pnutils

# Read in the gwtc-2.1 GW events from config file and write data file

In [43]:
def get_gwname():
    file = glob.glob('/work/yifan.wang/GWOSC-data/gwtc_2p1/config/data-*.ini')
    #file.remove('/work/yifan.wang/ringdown/t7-3ogc_fixpsd/3ogc_github_config/inference-gw190521_030229_emconstrained.ini')
    gwname = []
    for f in file:
        fname = os.path.basename(f)
        gwname.append(fname.split('-')[1][:15])
    gwname.remove('GW190425_081805')
    gwname.sort()
    return gwname

gwname = get_gwname()
np.size(gwname)

43

In [44]:
gwname

['GW190403_051519',
 'GW190408_181802',
 'GW190412_053044',
 'GW190413_052954',
 'GW190413_134308',
 'GW190421_213856',
 'GW190426_190642',
 'GW190503_185404',
 'GW190512_180714',
 'GW190513_205428',
 'GW190514_065416',
 'GW190517_055101',
 'GW190519_153544',
 'GW190521_030229',
 'GW190521_074359',
 'GW190527_092055',
 'GW190602_175927',
 'GW190620_030421',
 'GW190630_185205',
 'GW190701_203306',
 'GW190706_222641',
 'GW190707_093326',
 'GW190708_232457',
 'GW190719_215514',
 'GW190720_000836',
 'GW190725_174728',
 'GW190727_060333',
 'GW190728_064510',
 'GW190731_140936',
 'GW190803_022701',
 'GW190805_211137',
 'GW190814_211039',
 'GW190828_063405',
 'GW190828_065509',
 'GW190910_112807',
 'GW190915_235702',
 'GW190916_200658',
 'GW190917_114630',
 'GW190924_021846',
 'GW190925_232845',
 'GW190926_050336',
 'GW190929_012149',
 'GW190930_133541']

In [45]:
import lal

def gwinfo(name):
    # read in the GWTC-3 posterior files (cosmo means cosmologically reweighted)
    
    h5file = glob.glob('/work/yifan.wang/ringdown/t9_usev2data_3ogc/GWTC-2.1/*'+str(name)+'*.h5')
    # if not found
    if h5file ==[]:
        h5file = glob.glob('/work/yifan.wang/ringdown/t9_usev2data_3ogc/GWTC-2/all_posterior_samples/'+str(name)+'_comoving.h5') 
    # if not found
    if h5file == []:
        h5file = glob.glob('/work/yifan.wang/ringdown/t9_usev2data_3ogc/GWTC-2/all_posterior_samples/'+str(name[:8])+'_comoving.h5')
    print(h5file)
    if np.size(h5file)!=1:
        print('Error!!!')
        sys.exit(1)
    f = h5py.File(h5file[0],'r')
    # ra, dec, mass
    try:
        maxl_i = np.argmax(f['PublicationSamples']['posterior_samples']['log_likelihood'][:])
        waveform = 'PublicationSamples'
    except KeyError:
        maxl_i = np.argmax(f['IMRPhenomXPHM_comoving']['posterior_samples']['log_likelihood'][:])
        waveform = 'IMRPhenomXPHM_comoving'
    ra = f[waveform]['posterior_samples']['ra'][maxl_i]
    dec = f[waveform]['posterior_samples']['dec'][maxl_i]
    final_mass = f[waveform]['posterior_samples']['final_mass'][maxl_i]
    tref = f[waveform]['posterior_samples']['geocent_time'][maxl_i]
    m1 = f[waveform]['posterior_samples']['mass_1'][maxl_i]
    m2 = f[waveform]['posterior_samples']['mass_2'][maxl_i]
    spin1z = f[waveform]['posterior_samples']['spin_1z'][maxl_i]
    spin2z = f[waveform]['posterior_samples']['spin_2z'][maxl_i]
    
    # starting time = merger time + 10 M_f 
    toffset = 10* final_mass * lal.MTSUN_SI

    final_freq = pnutils.get_final_freq('SEOBNRv4',m1,m2,spin1z,spin2z)
    f.close()
    return ra,dec,final_mass,final_freq,toffset,tref

In [46]:
try:
    os.remove(events_dir)
except FileNotFoundError:
    pass
with open(events_dir, 'w') as t:
    for ii in gwname:
        print(ii)
        ra,dec,final_mass,final_freq,toffset,tref = gwinfo(ii)
        datafdir = glob.glob('/work/yifan.wang/GWOSC-data/gwtc_2p1/config/data-'+str(ii)+'.ini')
        print(datafdir)
        if np.size(datafdir)!=1:
            print('Error!!!')
            sys.exit(1)
        datafdir = datafdir[0]
        #start to write the events.ini
        t.write('[event-'+str(ii)+']\n')
        t.write('label='+str(ii)+'\n')
        t.write('config-files='+str(datafdir)+'\n')
        t.write('\t\t\t'+str(kerr_dir)+'\n')
        t.write('\t\t\t psd.ini \n')
        t.write('config-overrides =data:trigger-time:'+str(tref)+'\n')
        t.write('\t\t\tstatic_params:ra:'+str(ra)+'\n')
        t.write('\t\t\tstatic_params:dec:'+str(dec)+'\n')
        if final_mass < 150 and final_mass>10:
            t.write('\t\t\tprior-final_mass:min-final_mass:10\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:250\n')
        elif final_mass <= 10:
            t.write('\t\t\tprior-final_mass:min-final_mass:1\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:50\n')
        else:
            t.write('\t\t\tprior-final_mass:min-final_mass:100\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:500\n')

        if final_freq > 1024:
            t.write('\t\t\tdata:sample-rate:4096\n')
        t.write('\n')
t.close()

GW190403_051519
['/work/yifan.wang/ringdown/t9_usev2data_3ogc/GWTC-2.1/IGWN-GWTC2p1-v1-GW190403_051519_PEDataRelease.h5']
['/work/yifan.wang/GWOSC-data/gwtc_2p1/config/data-GW190403_051519.ini']
GW190408_181802
['/work/yifan.wang/ringdown/t9_usev2data_3ogc/GWTC-2/all_posterior_samples/GW190408_181802_comoving.h5']
['/work/yifan.wang/GWOSC-data/gwtc_2p1/config/data-GW190408_181802.ini']
GW190412_053044
['/work/yifan.wang/ringdown/t9_usev2data_3ogc/GWTC-2/all_posterior_samples/GW190412_comoving.h5']
['/work/yifan.wang/GWOSC-data/gwtc_2p1/config/data-GW190412_053044.ini']
GW190413_052954
['/work/yifan.wang/ringdown/t9_usev2data_3ogc/GWTC-2/all_posterior_samples/GW190413_052954_comoving.h5']
['/work/yifan.wang/GWOSC-data/gwtc_2p1/config/data-GW190413_052954.ini']
GW190413_134308
['/work/yifan.wang/ringdown/t9_usev2data_3ogc/GWTC-2/all_posterior_samples/GW190413_134308_comoving.h5']
['/work/yifan.wang/GWOSC-data/gwtc_2p1/config/data-GW190413_134308.ini']
GW190421_213856
['/work/yifan.wang/r

['/work/yifan.wang/GWOSC-data/gwtc_2p1/config/data-GW190930_133541.ini']
